<a href="https://colab.research.google.com/github/Actulus/IntelligensModszerekTantargy/blob/main/Scikit_learn_osztalyozok.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [58]:
!pip install -U scikit-learn
!pip install six

In [60]:
import numpy as np
from sklearn.neural_network import MLPClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier

from six import StringIO
from sklearn.tree import export_graphviz
import pydot
from IPython.display import Image

**1. feladat: adatok betöltése**

(a) Az adatok szemrevételezésével határozza meg az elválasztókarakter (delimiter) értékét!

In [6]:
delimiter = ','
data_with_labels = np.loadtxt('https://archive.ics.uci.edu/ml/machine-learning-databases/spambase/spambase.data', delimiter=delimiter)
data_with_labels

array([[0.000e+00, 6.400e-01, 6.400e-01, ..., 6.100e+01, 2.780e+02,
        1.000e+00],
       [2.100e-01, 2.800e-01, 5.000e-01, ..., 1.010e+02, 1.028e+03,
        1.000e+00],
       [6.000e-02, 0.000e+00, 7.100e-01, ..., 4.850e+02, 2.259e+03,
        1.000e+00],
       ...,
       [3.000e-01, 0.000e+00, 3.000e-01, ..., 6.000e+00, 1.180e+02,
        0.000e+00],
       [9.600e-01, 0.000e+00, 0.000e+00, ..., 5.000e+00, 7.800e+01,
        0.000e+00],
       [0.000e+00, 0.000e+00, 6.500e-01, ..., 5.000e+00, 4.000e+01,
        0.000e+00]])

(b) Az utolsó oszlop tartalmazza a célvátozó (más néven: címke, label) értékét (a konkrét esetben azt, hogy az adott e-mail spam-e vagy sem). Válassza le a célváltozót az adatokról, azaz hozzon létre *data*  ill. *labels* elnevezésű np.array-eket, amelyek csak az adatokat (célvátozó nélkül) illetve csak a célváltozót tartalmazzák! Ellenőrizze az eredeti és a létrehozott tömbök méretét!

In [8]:
data = np.array(data_with_labels[:, :-1])
data.shape

(4601, 57)

In [9]:
labels = np.array(data_with_labels[:, -1])
labels.shape

(4601,)

(c) Bontsa fel az adatokat és a hozzájuk tartozó címkéket tanító- és tesztadatokra. Minden 5-dik példány, azaz a 4, 9, 14... indexű példányok kerüljenek a teszthalmazba, a többi pedig a tanítóhalmazba! Ehhez első lépésként hozzon létre két np.array-t, amelyek a tanító és tesztpéldányok indexeit tartalmazzák, majd ezeket használva bontsa fel az adatokat és címkéket tanító- és tesztadatokra *data_train*, *data_test* ill. *labels_train* és *labels_test* néven!

In [10]:
test_indices = np.arange(4, len(data), 5)
train_indices = np.setdiff1d(np.arange(len(data)), test_indices)

In [11]:
data_train   = data[train_indices]
data_test    = data[test_indices]
labels_train = labels[train_indices]
labels_test  = labels[test_indices]

(d) Az operációs rendszer *wget* parancsával töltse le a

https://archive.ics.uci.edu/ml/machine-learning-databases/spambase/spambase.names

fájlt és jelenítse meg az első 50 sorát a *head* paranccsal!

Olvassa be a fájlból az oszlopneveket a *column_names* tömbbe!
(Segítség: legelső oszlop neve a fájl 34-dik sorában található.)

In [12]:
!wget https://archive.ics.uci.edu/ml/machine-learning-databases/spambase/spambase.names

--2025-03-28 16:07:22--  https://archive.ics.uci.edu/ml/machine-learning-databases/spambase/spambase.names
Resolving archive.ics.uci.edu (archive.ics.uci.edu)... 128.195.10.252
Connecting to archive.ics.uci.edu (archive.ics.uci.edu)|128.195.10.252|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified
Saving to: ‘spambase.names’

spambase.names          [ <=>                ]   3.48K  --.-KB/s    in 0s      

2025-03-28 16:07:22 (546 MB/s) - ‘spambase.names’ saved [3566]



In [13]:
!head -n 50 spambase.names

| SPAM E-MAIL DATABASE ATTRIBUTES (in .names format)
|
| 48 continuous real [0,100] attributes of type word_freq_WORD 
| = percentage of words in the e-mail that match WORD,
| i.e. 100 * (number of times the WORD appears in the e-mail) / 
| total number of words in e-mail.  A "word" in this case is any 
| string of alphanumeric characters bounded by non-alphanumeric 
| characters or end-of-string.
|
| 6 continuous real [0,100] attributes of type char_freq_CHAR
| = percentage of characters in the e-mail that match CHAR,
| i.e. 100 * (number of CHAR occurences) / total characters in e-mail
|
| 1 continuous real [1,...] attribute of type capital_run_length_average
| = average length of uninterrupted sequences of capital letters
|
| 1 continuous integer [1,...] attribute of type capital_run_length_longest
| = length of longest uninterrupted sequence of capital letters
|
| 1 continuous integer [1,...] attribute of type capital_run_length_total
| = sum of length of uninterrupted sequences of

In [20]:
column_names = []

with open('spambase.names') as f:
  for _ in range(33):
      next(f)

  # Read the column names starting from the 34th line onward
  for line in f:
      # Append each line to column_names, splitting by commas if needed
      column_names.append(line.strip())

In [21]:
column_names

['word_freq_make:         continuous.',
 'word_freq_address:      continuous.',
 'word_freq_all:          continuous.',
 'word_freq_3d:           continuous.',
 'word_freq_our:          continuous.',
 'word_freq_over:         continuous.',
 'word_freq_remove:       continuous.',
 'word_freq_internet:     continuous.',
 'word_freq_order:        continuous.',
 'word_freq_mail:         continuous.',
 'word_freq_receive:      continuous.',
 'word_freq_will:         continuous.',
 'word_freq_people:       continuous.',
 'word_freq_report:       continuous.',
 'word_freq_addresses:    continuous.',
 'word_freq_free:         continuous.',
 'word_freq_business:     continuous.',
 'word_freq_email:        continuous.',
 'word_freq_you:          continuous.',
 'word_freq_credit:       continuous.',
 'word_freq_your:         continuous.',
 'word_freq_font:         continuous.',
 'word_freq_000:          continuous.',
 'word_freq_money:        continuous.',
 'word_freq_hp:           continuous.',


**2. feladat: logisztikus regresszió**

(a) Egészítse ki a kódot azzal, hogy kiszámolja az osztályozó pontosságát, azaz a helyesen prediktált tesztpéldányok arányát!

(b) Alapbeállítás szerint mennyi a komplexitási tényező (C) értéke? Tanulmányozza a dokumentációt: https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html . Állítsa C értékét 10-re, tanítsa a modellt és mérje le a pontosságát a teszt halmazon!

In [22]:
from sklearn.linear_model import LogisticRegression

In [23]:
model = LogisticRegression()
model.fit(data_train, labels_train)

/usr/local/lib/python3.11/dist-packages/sklearn/linear_model/_logistic.py:465: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


LogisticRegression()

In [26]:
pred = model.predict(data_test)

In [27]:
accuracy = (pred == labels_test).mean()
accuracy

np.float64(0.9130434782608695)

In [34]:
model2 = LogisticRegression(C=0.1)
model2.fit(data_train, labels_train)

/usr/local/lib/python3.11/dist-packages/sklearn/linear_model/_logistic.py:465: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


LogisticRegression(C=0.1)

In [35]:
pred2 = model.predict(data_test)

In [36]:
accuracy2 = (pred == labels_test).mean()
accuracy2

np.float64(0.9130434782608695)

**3. feladat: Neurális hálók**

A scikit-learn osztályozói standard interface-t valósítanak meg, rendelkeznek többek között *fit* és *predict* metódusokkal (a modell tanításához ill. új adatra történő predikciók számításához).

(a) Annak ismeretében, hogy az előrecsatolt neurális hálókat a *sklearn.neural_network* csomagon belüli *MLPClassifier* (multilayer perceptron classifer) elnevezésű osztály implementálja, tanítson egy neurális hálót a spam felismerési feladatra és mérje le a háló pontosságát!

In [40]:
# Initialize the MLPClassifier
mlp = MLPClassifier(random_state=1, max_iter=300)

# Train the neural network
mlp.fit(data_train, labels_train)

# Make predictions on the test set
mlp_pred = mlp.predict(data_test)

# Calculate the accuracy of the neural network
mlp_accuracy = (mlp_pred == labels_test).mean()
print(f"Neural Network Accuracy: {mlp_accuracy}")


Neural Network Accuracy: 0.9239130434782609


(b) Hány belső (rejtett) réteggel rendelkezik a tanított háló? Mennyi a unitok száma az egyes rétegekben? Változtassa meg a háló architektúráját úgy, hogy két rejtett réteggel rendelkezzen és mindkét rétegben 10-10 unit legyen! Tanítsa és értékelje ki a modellt!

In [41]:
print(f"Number of hidden layers: {mlp.n_layers_ - 2}") # Output the number of hidden layers
print(f"Number of units per hidden layer: {mlp.hidden_layer_sizes}") # Output the number of units in each hidden layer


# Modified neural network with two hidden layers, each with 10 units
mlp_modified = MLPClassifier(hidden_layer_sizes=(10, 10), random_state=1, max_iter=300)

# Train the modified neural network
mlp_modified.fit(data_train, labels_train)

# Make predictions on the test set using the modified network
mlp_modified_pred = mlp_modified.predict(data_test)

# Calculate the accuracy of the modified neural network
mlp_modified_accuracy = (mlp_modified_pred == labels_test).mean()
print(f"Modified Neural Network Accuracy: {mlp_modified_accuracy}")


Number of hidden layers: 1
Number of units per hidden layer: (100,)
Modified Neural Network Accuracy: 0.9239130434782609


(c) Változtassa meg az aktivációs függvényt a szigmoid függvényre, tanítsa és értékelje ki a modellt!


In [42]:
# Modified neural network with sigmoid activation function
mlp_sigmoid = MLPClassifier(hidden_layer_sizes=(10, 10), activation='logistic', random_state=1, max_iter=300)

# Train the modified neural network
mlp_sigmoid.fit(data_train, labels_train)

# Make predictions on the test set using the modified network
mlp_sigmoid_pred = mlp_sigmoid.predict(data_test)

# Calculate the accuracy of the modified neural network
mlp_sigmoid_accuracy = (mlp_sigmoid_pred == labels_test).mean()
print(f"Modified Neural Network with Sigmoid Activation Accuracy: {mlp_sigmoid_accuracy}")


Modified Neural Network with Sigmoid Activation Accuracy: 0.941304347826087


(d) A pytorch-beli neurális hálókkal összehasonlítva, mit mondana a scikit-learn-beli implementációról? Melyikkel könnyebb dolgozni?

In [43]:
# scikit-learn-nel konnyebb az implementacio, viszont PyTorchban tobb lehetoseg van egy bonyolultabb modell felepitesere

**4. feladat: legközelebbi szomszéd osztályozó**

A legközelebbi szomszéd osztályozót az *sklearn.neighbors* csomagon belüli *KNeighborsClassifier* implementálja.

(a) Osztályozza a tesztadatok legközelebbi szomszéd osztályozóval és mérje le az osztályozó pontosságát!

In [45]:
# Initialize the KNeighborsClassifier
knn = KNeighborsClassifier()

# Train the classifier
knn.fit(data_train, labels_train)

# Make predictions on the test set
knn_pred = knn.predict(data_test)

# Calculate the accuracy
knn_accuracy = (knn_pred == labels_test).mean()
print(f"K-Nearest Neighbors Accuracy: {knn_accuracy}")


K-Nearest Neighbors Accuracy: 0.8021739130434783


(b) Mit jelent a "tanítás" a legközelebbi szomszéd osztályozó esetében? Mi történik a *fit* metódus meghívásakor?

In [ ]:
# A "tanítás" a legközelebbi szomszéd osztályozó esetében nem a hagyományos értelemben vett modellparaméterek optimalizálását jelenti, mint például a neurális hálóknál vagy a logisztikus regressziónál.  A *fit* metódus meghívásakor az osztályozó egyszerűen *memóriába tölti* a tanító adatokat (és a hozzájuk tartozó címkéket).  Nincsenek olyan paraméterek, amiket a tanító adatok alapján módosítana.

# A predikció során, amikor egy új adatpont osztályozására kerül sor, a modell megkeresi a tanítóhalmazban azt a *k* darab adatpontot, amelyik a legközelebb van az új adatponthoz (ezt általában euklideszi távolság alapján számolják). Az új adatpont osztályát a *k* legközelebbi szomszéd címkéinek többségi szavazásával határozza meg.


(c) Mennyi volt az előző alkalommal a legközelebbi szomszédok száma? Milyen eredményt kapunk, ha a legközelebbi szomszédok számát 1-re vagy 10-re állítjuk?

In [47]:
print(f"Previous k value: {knn.n_neighbors}")

knn_1 = KNeighborsClassifier(n_neighbors=1)
knn_1.fit(data_train, labels_train)
knn_1_pred = knn_1.predict(data_test)
knn_1_accuracy = (knn_1_pred == labels_test).mean()
print(f"K-Nearest Neighbors Accuracy (k=1): {knn_1_accuracy}")

knn_10 = KNeighborsClassifier(n_neighbors=10)
knn_10.fit(data_train, labels_train)
knn_10_pred = knn_10.predict(data_test)
knn_10_accuracy = (knn_10_pred == labels_test).mean()
print(f"K-Nearest Neighbors Accuracy (k=10): {knn_10_accuracy}")


Previous k value: 5
K-Nearest Neighbors Accuracy (k=1): 0.8173913043478261
K-Nearest Neighbors Accuracy (k=10): 0.8032608695652174


(d) Az ún. *Minkowski távolság* az euklideszi távolság és Manhattan-távolság közös általánosítása: p=2 mellett adódik az euklideszi távolság, p=1-re pedig a Manhattan távolság. Használjon Manhattan távolságot az osztályozás során!

In [48]:
knn_manhattan = KNeighborsClassifier(n_neighbors=10, p=1)  # p=1 corresponds to Manhattan distance
knn_manhattan.fit(data_train, labels_train)
knn_manhattan_pred = knn_manhattan.predict(data_test)
knn_manhattan_accuracy = (knn_manhattan_pred == labels_test).mean()
print(f"K-Nearest Neighbors Accuracy (Manhattan distance): {knn_manhattan_accuracy}")


K-Nearest Neighbors Accuracy (Manhattan distance): 0.8369565217391305


**5. feladat: Naive Bayes**

A naive Bayes osztályozó (egyik változatát) az *sklearn.naive_bayes* csomagon belüli *GaussianNB* implementálja. Tanítson egy *GaussianNB*-t és mérje le az osztályozó pontosságát!

In [50]:
# Initialize the Gaussian Naive Bayes classifier
gnb = GaussianNB()

# Train the classifier
gnb.fit(data_train, labels_train)

# Make predictions on the test set
gnb_pred = gnb.predict(data_test)

# Calculate the accuracy
gnb_accuracy = (gnb_pred == labels_test).mean()
print(f"Gaussian Naive Bayes Accuracy: {gnb_accuracy}")


Gaussian Naive Bayes Accuracy: 0.8173913043478261


**6. feladat: Döntési fák**

(a) A döntési fákat az sklearn.tree csomagon belüli DecisionTreeClassifier implementálja. Készítsen egy döntési fát és mérje le az osztályozó pontosságát!

In [52]:
# Initialize the DecisionTreeClassifier
dtc = DecisionTreeClassifier()

# Train the classifier
dtc.fit(data_train, labels_train)

# Make predictions on the test set
dtc_pred = dtc.predict(data_test)

# Calculate the accuracy
dtc_accuracy = (dtc_pred == labels_test).mean()
print(f"Decision Tree Accuracy: {dtc_accuracy}")


Decision Tree Accuracy: 0.907608695652174


(b) Módosítsa az előbbi kódot úgy, hogy a létrehozott döntési fa mélysége legfeljebb 4 legyen!

In [53]:
dtc_depth4 = DecisionTreeClassifier(max_depth=4)

# Train the classifier
dtc_depth4.fit(data_train, labels_train)

# Make predictions on the test set
dtc_depth4_pred = dtc_depth4.predict(data_test)

# Calculate the accuracy
dtc_depth4_accuracy = (dtc_depth4_pred == labels_test).mean()
print(f"Decision Tree Accuracy (max_depth=4): {dtc_depth4_accuracy}")


Decision Tree Accuracy (max_depth=4): 0.8869565217391304


A döntési fa ábrázolása

In [62]:
dot_data = StringIO()
export_graphviz(dtc, out_file=dot_data, feature_names=column_names, \
                    class_names=['not spam', 'spam'], filled=True, rounded=True, \
                    special_characters=True)
graph = pydot.graph_from_dot_data(dot_data.getvalue())
Image(graph[0].create_png())